In [ ]:
!pip install PyPDF2

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 232.6/232.6 kB 4.4 MB/s eta 0:00:00


In [ ]:
from google import genai
import re
import pandas as pd

## Using Gemini to produce CSV from PDF

# Automating the entire pipeline

How It Works

1. Extract Webpage Text: The function extract_webpage_text uses the URL to fetch the webpage content and extracts the text using Selenium.

2. Gemini API Call: The forum_data_scraper function appends a prompt instructing Gemini to output forum details in a specific annotated format, then calls llm_call.

3. Parsing the Response: The forum_data_to_dataframe function uses a regex pattern to extract the annotated details and then converts them into a Pandas DataFrame.

4. Saving the Data: The resulting DataFrame is then saved as a CSV file.

https://www.scrapingbee.com/blog/selenium-python/

In [ ]:
!pip install selenium

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.4/9.4 MB 16.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 492.9/492.9 kB 10.6 MB/s eta 0:00:00


# Integrating with dataframe containing all urls extracted

In [ ]:
# forum_scraper_colab.py - saving to drive automatically
import re
import requests
import tempfile
import shutil
from bs4 import BeautifulSoup
import json
import pandas as pd
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
import time
import os
from datetime import datetime
from IPython.display import display

# Mount Google Drive
from google.colab import drive

drive.mount('/content/drive')

# --- Gemini API Call Function ---
def llm_call(prompt):
    client = genai.Client(api_key="_")
    response = client.models.generate_content(
        model="gemini-2.0-flash", contents=prompt
    )
    return response.text

# --- Selenium-Based Webpage Text Extraction ---
def extract_webpage_text_with_selenium(url):
    chrome_options = Options()
    chrome_options.add_argument("--headless=new")
    chrome_options.add_argument("--no-sandbox")
    chrome_options.add_argument("--disable-dev-shm-usage")
    chrome_options.add_argument("user-agent=Mozilla/5.0 (Windows NT 10.0; Win64; x64) Chrome/115.0 Safari/537.36")
    temp_dir = tempfile.mkdtemp(prefix="chrome-profile-")
    chrome_options.add_argument(f"--user-data-dir={temp_dir}")

    driver = webdriver.Chrome(options=chrome_options)
    driver.get(url)
    time.sleep(5)
    text = driver.find_element("tag name", "body").text
    driver.quit()
    shutil.rmtree(temp_dir)
    return text

# --- Gemini Prompt for Forum Data Extraction ---
def forum_data_scraper(page_text):
    command = """
    Extract the following details for each forum post from the provided text:
    - Comment: The text of the comment.
    - Username: The username of the poster.
    - Upvote: The number of upvotes (as a number, or empty string if not provided).
    - Parent Comment: The text of the parent comment if this comment is a reply, or empty string if not provided.
    - Forum Content: The full content of the forum post.
    - Forum Title: The title of the forum thread.

    Format each forum post's information as follows:
    @Comment: 'Example comment', Username: 'user123', Upvote: '10', Parent Comment: 'Parent comment text', Forum Content: 'The full text of the forum post', Forum Title: 'Forum Title'@

    If no forum post information is found, return exactly: @No forum info@
    """
    prompt = page_text + command
    return llm_call(prompt)

# --- Regex Parsing Function to Create DataFrame ---
def forum_data_to_dataframe(llm_response):
    pattern = r"@\s*Comment:\s*['\"](.*?)['\"],\s*Username:\s*'(.*?)',\s*Upvote:\s*'(.*?)',\s*Parent Comment:\s*'(.*?)',\s*Forum Content:\s*['\"](.*?)['\"],\s*Forum Title:\s*'(.*?)'@"
    matches = re.findall(pattern, llm_response, re.DOTALL)

    if not matches:
        print("No valid forum information extracted. Raw response:")
        print(llm_response)
        return None

    data = []
    for match in matches:
        comment, username, upvote, parent_comment, forum_content, forum_title = match
        upvote_val = int(upvote.strip()) if upvote.strip().isdigit() else None

        data.append({
            'comment': comment.strip(),
            'username': username.strip(),
            'upvote': upvote_val,
            'parent_comment': parent_comment.strip(),
            'forum_content': forum_content.strip(),
            'forum_title': forum_title.strip()
        })

    return pd.DataFrame(data)

# --- Batch Splitter ---
def split_into_batches(urls, batch_size):
    return [urls[i:i + batch_size] for i in range(0, len(urls), batch_size)]

# --- Process Multiple Forum URLs ---
def process_forum_urls(urls, partial_path):
    all_dfs = []
    for url in urls:
        print("Processing URL:", url)
        try:
            web_text = extract_webpage_text_with_selenium(url)
            print("Extracted text length:", len(web_text))
            llm_response = forum_data_scraper(web_text)
            df = forum_data_to_dataframe(llm_response)
            if df is not None:
                df["source_url"] = url  # Track original URL for deduplication
                df.to_csv(partial_path, index=False)  # Save partial progress to Drive
                all_dfs.append(df)
            else:
                print("No data extracted.")
        except Exception as e:
            print("Error processing URL:", url)
            print(e)
    return pd.concat(all_dfs, ignore_index=True) if all_dfs else None

# --- Main Execution Block ---
if __name__ == '__main__':
    try:
        df_forums = pd.read_csv("uberppl_forum_urls_FINAL.csv")
        forum_urls = df_forums["url"].tolist()
    except Exception as e:
        print("Error loading URLs:", e)
        forum_urls = []

    batch_size = 5
    url_batches = split_into_batches(forum_urls, batch_size)

    # Save paths in the shortcut folder to shared Drive
    drive_base = "/content/drive/MyDrive/destination_filters_research"
    output_file = os.path.join(drive_base, "combined_forum_data.csv")
    partial_path = os.path.join(drive_base, "latest_partial_batch.csv")

    if os.path.exists(output_file):
        df_existing = pd.read_csv(output_file)
        processed_urls = set(df_existing["source_url"].unique()) if "source_url" in df_existing.columns else set()
    else:
        df_existing = pd.DataFrame()
        processed_urls = set()

    for idx, batch in enumerate(url_batches):
        print(f"\n--- Batch {idx + 1}/{len(url_batches)} ---")
        batch = [url for url in batch if url not in processed_urls]

        if not batch:
            print("Batch already processed. Skipping.")
            continue

        batch_df = process_forum_urls(batch, partial_path)
        if batch_df is not None:
            df_existing = pd.concat([df_existing, batch_df], ignore_index=True)
            df_existing.to_csv(output_file, index=False)
            print(f"✅ Saved batch {idx + 1}. Total rows: {len(df_existing)}")

            print("Latest batch preview:")
            display(batch_df.head())

            print("Full combined preview (last 5 rows):")
            display(df_existing.tail())

        else:
            print(f"❌ No data from batch {idx + 1}")

        print("Pausing briefly...")
        time.sleep(10)


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).

--- Batch 1/100 ---
Processing URL: https://www.uberpeople.net/threads/destination-filter-are-no-longer-a-thing-fuber-new-low.483686/post-7720393
Extracted text length: 5963
Processing URL: https://www.uberpeople.net/threads/destination-filter.465208/post-7449760
Extracted text length: 5045
Processing URL: https://www.uberpeople.net/threads/destination-filter-experience.479034/post-7655610
Extracted text length: 2828
Processing URL: https://www.uberpeople.net/threads/destination-filter-frustrating.447044/post-7167229
Extracted text length: 29220
Processing URL: https://www.uberpeople.net/threads/destination-filter-not-working.460053/post-7376521
Extracted text length: 9994
✅ Saved batch 1. Total rows: 72
Latest batch preview:


comment        username upvote  \
0  Destination Filter is now a thing of the past,...         coolblk   None   
1  Uninstall and reinstall the Uber driver app it...  ObeyTheNumbers   None   
2                                     Fine on my end    tonytone1908   None   
3  They're screwing with DF in Chicago again too ...        uber_312   None   
4  ... they also forced me to upgrade my version ...        uber_312   None   

  parent_comment                                      forum_content  \
0                 Destination Filter is now a thing of the past,...   
1                 Uninstall and reinstall the Uber driver app it...   
2                             Fine on my end\nReactions:\nUL Lurker   
3                 They're screwing with DF in Chicago again too ...   
4                 ... they also forced me to upgrade my version ...   

                                         forum_title  \
0  Destination Filter are no longer a thing FUber...   
1  Destination Filter are no longer a thing FUber...   
2  Destination Filter are no longer a thing FUber...   
3  Destination Filter are no longer a thing FUber...   
4  Destination Filter are no longer a thing FUber...   

                                          source_url  
0  https://www.uberpeople.net/threads/destination...  
1  https://www.uberpeople.net/threads/destination...  
2  https://www.uberpeople.net/threads/destination...  
3  https://www.uberpeople.net/threads/destination...  
4  https://www.uberpeople.net/threads/destination...

Full combined preview (last 5 rows):


comment     username upvote  \
67  I'm in L.A. California but I mean , When UBER ...  Slingshot@u   None   
68  Does the destination filter actually work for ...    garyq0430   None   
69  partimeuberdc said:\nUse the Destination Filte...   Alex in SF   None   
70  I’m able to reset my app by turning the phone ...   Alex in SF   None   
71  It's not that they're not available, at least ...    garyq0430   None   

                                       parent_comment  \
67                                                      
68                                                      
69  Use the Destination Filter every day before my...   
70                                                      
71                                                      

                                        forum_content  \
67  I'm in L.A. California but I mean , When UBER ...   
68  Does the destination filter actually work for ...   
69  partimeuberdc said:\nUse the Destination Filte...   
70  I’m able to reset my app by turning the phone ...   
71  It's not that they're not available, at least ...   

                       forum_title  \
67  Destination Filter not working   
68  Destination Filter not working   
69  Destination Filter not working   
70  Destination Filter not working   
71  Destination Filter not working   

                                           source_url  
67  https://www.uberpeople.net/threads/destination...  
68  https://www.uberpeople.net/threads/destination...  
69  https://www.uberpeople.net/threads/destination...  
70  https://www.uberpeople.net/threads/destination...  
71  https://www.uberpeople.net/threads/destination...

Pausing briefly...

--- Batch 2/100 ---
Processing URL: https://www.uberpeople.net/threads/destination-filter.307307/post-4688085
Extracted text length: 15850
Processing URL: https://www.uberpeople.net/threads/destination-filter-not-letting-me-accept-trips.460938/post-7389178
Extracted text length: 10364
Processing URL: https://www.uberpeople.net/threads/destination-filter.471597/post-7547100
Extracted text length: 11946
Processing URL: https://www.uberpeople.net/threads/destination-filter-no-longer-working.504290/post-8049775
Extracted text length: 4424
Processing URL: https://www.uberpeople.net/threads/destination-filter-not-working-complaints-accc.443957/post-7114289
Extracted text length: 2946
✅ Saved batch 2. Total rows: 135
Latest batch preview:


...

✅ Saved batch 100. Total rows: 4737
Latest batch preview:


comment            username  \
0  Is it me or has it gotten 10x worse. I put in ...           Tysmith95   
1                    No it has always been that bad.             Jaackil   
2  it is certainly less definitive. i have notice...  B - uberlyftdriver   
3  It did seem better when we had the trip prefer...             Jaackil   
4  Same here. I don't use it anymore because of t...          MaineMasai   

   upvote parent_comment                                      forum_content  \
0     NaN                 Home\nForums\nGeographical\nUS Cities\nNorthea...   
1     NaN                                   No it has always been that bad.   
2     NaN                 it is certainly less definitive. i have notice...   
3     NaN                 It did seem better when we had the trip prefer...   
4     NaN                 Same here. I don't use it anymore because of t...   

          forum_title                                         source_url  
0  Destination filter  https://www.uberpeople.net/threads/destination...  
1  Destination filter  https://www.uberpeople.net/threads/destination...  
2  Destination filter  https://www.uberpeople.net/threads/destination...  
3  Destination filter  https://www.uberpeople.net/threads/destination...  
4  Destination filter  https://www.uberpeople.net/threads/destination...

Full combined preview (last 5 rows):


comment            username  \
4732  Not sure if everyone know it but this shit cha...                ROTA   
4733  It's really BS that it shuts itself off. Like ...           Tysmith95   
4734  I was gonna post the same exact thing the othe...            CharlesG   
4735  its there passive aggressive way to run with n...  B - uberlyftdriver   
4736  Lyft's DF is soooooooooooooo bad. Sent me to S...               scamp   

     upvote                                     parent_comment  \
4732    NaN                                                      
4733    NaN                                                      
4734    NaN                                                      
4735    NaN                                                      
4736    NaN  Not sure if everyone know it but this shit cha...   

                                          forum_content  \
4732  Not sure if everyone know it but this shit cha...   
4733  It's really BS that it shuts itself off. Like ...   
4734  I was gonna post the same exact thing the othe...   
4735  its there passive aggressive way to run with n...   
4736  ROTA said:\nNot sure if everyone know it but t...   

                  forum_title  \
4732  Lyft Destination Filter   
4733  Lyft Destination Filter   
4734  Lyft Destination Filter   
4735  Lyft Destination Filter   
4736  Lyft Destination Filter   

                                             source_url  
4732  https://www.uberpeople.net/threads/lyft-destin...  
4733  https://www.uberpeople.net/threads/lyft-destin...  
4734  https://www.uberpeople.net/threads/lyft-destin...  
4735  https://www.uberpeople.net/threads/lyft-destin...  
4736  https://www.uberpeople.net/threads/lyft-destin...

Pausing briefly...
